Example of anomaly detection using symmetric Variational Autoencoder as in
 Pu, Yunchen, et al. "Symmetric variational autoencoder and connections to adversarial learning." arXiv preprint arXiv:1709.01846 (2017).

In [1]:
using Plots
plotly()
import Plots: plot
clibrary(:Plots)
using JLD

code_path = "../src"

push!(LOAD_PATH, code_path)
using AnomalyDetection

In [2]:
# load data
dataset = load("toy_data_3.jld")["data"]
X = AnomalyDetection.Float.(dataset.data)
Y = dataset.labels;
nX = X[:,Y.==0]

2×90 Array{Float32,2}:
 0.803442  0.804605  0.807145  0.819485  …  0.0350314  0.0613807  0.0685027
 0.821998  0.834235  0.826129  0.848182     0.973926   1.00745    0.973256 

In [3]:
# sVAE settings
indim = size(X,1)
hiddendim = 10
latentdim = 2
nlayers = 2
N = size(nX,2)

# setup the VAE object
ensize = [indim; hiddendim; hiddendim; latentdim*2] # encoder architecture
decsize = [latentdim; hiddendim; hiddendim; indim] # decoder architecture
dissize = [indim + latentdim; hiddendim; hiddendim; 1] # discriminator architecture
lambda = 0.0 # weight of the data error term
threshold = 0 # classification threshold, is recomputed during fit!()
contamination = size(Y[Y.==1],1)/size(Y, 1) # for automatic threshold computation
iterations = 10000
cbit = 5000 # after this number of iteratiosn, callback is printed
verbfit = true
L = 50 # batchsize
M = 1 #  number of samples of X in reconstruction error
activation = Flux.relu
layer = Flux.Dense
rdelta = 1e-4 # reconstruction error threshold for training stopping
alpha = 0.5 # weighs between reconstruction error and discriminator score for classification
# 0 = only reconstruction error, 1 = only discriminator score
Beta = 1.0 # for automatic threshold computation, in [0, 1] 
# 1.0 = tight around normal samples
tracked = true # do you want to store training progress?
# it can be later retrieved from model.traindata
xsigma = 1.0 # static estimate of data variance
model = sVAEmodel(ensize, decsize, dissize, lambda, threshold, contamination, iterations, cbit, verbfit, 
    L, M = M, activation = activation, rdelta = rdelta, Beta = Beta, xsigma = xsigma,
    tracked = tracked, layer = layer)

AnomalyDetection.sVAEmodel(AnomalyDetection.sVAE(Chain(Dense(2, 10, NNlib.relu), Dense(10, 10, NNlib.relu), Dense(10, 4)), AnomalyDetection.sample_z, Chain(Dense(2, 10, NNlib.relu), Dense(10, 10, NNlib.relu), Dense(10, 2)), Chain(Dense(4, 10, NNlib.relu), Dense(10, 10, NNlib.relu), Dense(10, 1)), Chain(Dense(4, 10, NNlib.relu), Dense(10, 10, NNlib.relu), Dense(10, 1))), 0.0, 0, 0.1262135922330097, 10000, 5000, 50, 1, true, 0.0001f0, 0.5f0, 1.0f0, 1.0f0, MVHistory{ValueHistories.History})

In [4]:
# fit the model
AnomalyDetection.evalloss(model, nX)
AnomalyDetection.fit!(model, nX)
AnomalyDetection.evalloss(model, nX)

discriminator loss: 1.3895853826574431
VAE loss: -0.0018995269820520147
reconstruction error: 0.4221935316562756

discriminator loss: 1.40362617832335
VAE loss: -0.02902169277275403
reconstruction error: 0.12175360686007367

discriminator loss: 1.1697296246887556
VAE loss: 0.670225637050155
reconstruction error: 0.12128285668819778

discriminator loss: 1.1877432053528958
VAE loss: 0.6157907236419974
reconstruction error: 0.1107029145290894



In [5]:
"""
	plot(model)

Plot the model loss.
"""
function plot(model::sVAEmodel)
	# plot model loss
	if model.history == nothing
		println("No data to plot, set tracked = true before training.")
		return
	else
        p = plot(model.history[:discriminator_loss], title = "model loss", 
            label = "discriminator loss", 
            xlabel = "iteration", ylabel = "loss", 
            seriestype = :line, 
            markershape = :none)
        plot!(model.history[:vae_loss], label = "VAE loss",
            seriestype = :line, markershape = :none)
        plot!(model.history[:reconstruction_error], label = "reconstruction error",
            seriestype = :line, markershape = :none, 
            c = :green,
            title = "model loss")
        return p
    end
end


RecipesBase.plot

In [6]:
# plot model loss
display(plot(model))
if !isinteractive()
    gui()
end

In [7]:
# plot heatmap of the fit
xl = (minimum(X[1,:])-0.05, maximum(X[1,:]) + 0.05)
yl = (minimum(X[2,:])-0.05, maximum(X[2,:]) + 0.05)
p = scatter(X[1, Y.==0], X[2, Y.==0], c = :red, label = "data",
    xlims=xl, ylims = yl, title = "discriminator contours", 
    c=:green)
Xrec = Flux.Tracker.data(model(X[:, Y.==0]))
scatter!(Xrec[1,:], Xrec[2,:], label = "reconstructed")
Xgen = AnomalyDetection.generate(model, 30)
scatter!(Xgen[1,:], Xgen[2,:], label = "generated", c = :black, markersize = 3,
    legend = (0.1, 0.7))

x = linspace(xl[1], xl[2], 30)
y = linspace(yl[1], yl[2], 30)
zz = zeros(size(y,1),size(x,1))
for i in 1:size(y, 1)
    for j in 1:size(x, 1)
        _x = AnomalyDetection.Float.([x[j], y[i]])
        _z = AnomalyDetection.getcode(model, _x)
        zz[i,j] = Flux.Tracker.data(AnomalyDetection.discriminate(model, _x, _z))[1]
    end
end
contourf!(x, y, zz, c = :viridis)

display(p)
if !isinteractive()
    gui()
end


In [8]:
model(nX)

Tracked 2×90 Array{Float64,2}:
 0.655344  0.223615  0.675865  0.726451  …  0.742653  0.756658  0.777055
 0.701943  0.911551  0.691481  0.7631       0.777425  0.779693  0.800036

In [9]:
nX

2×90 Array{Float32,2}:
 0.803442  0.804605  0.807145  0.819485  …  0.0350314  0.0613807  0.0685027
 0.821998  0.834235  0.826129  0.848182     0.973926   1.00745    0.973256 

In [10]:
AnomalyDetection.mu(model, nX)

Tracked 2×90 Array{Float32,2}:
 0.000505357  0.000505357  0.000505357  …  0.000505357  0.000505357
 0.0369507    0.0369507    0.0369507       0.0369507    0.0369507  

In [11]:
AnomalyDetection.sigma(model, nX)

Tracked 2×90 Array{Float64,2}:
 1.10771  1.10771  1.10771  1.10771  …  1.10771  1.10771  1.10771  1.10771
 1.25414  1.25414  1.25414  1.25414     1.25414  1.25414  1.25414  1.25414

In [12]:
AnomalyDetection.sample_z(model, nX)

Tracked 2×90 Array{Float64,2}:
 -0.199187  0.418121  1.21583  0.68148  …  -0.0136677  1.65836   0.935702
  0.966233  0.633791  1.72329  1.7978      -0.15611    1.96335  -0.243804

In [13]:
# predict labels
AnomalyDetection.setthreshold!(model, X)
model.M = 20 # number of samples - for classification higher is better (more stable)
tryhat = AnomalyDetection.predict(model, X)

103-element Array{Int64,1}:
 0
 0
 0
 0
 0
 0
 0
 0
 0
 0
 0
 0
 0
 ⋮
 0
 1
 1
 0
 1
 0
 1
 0
 1
 0
 0
 1

In [14]:
# get the labels and roc stats
tryhat, tstyhat = AnomalyDetection.rocstats(dataset, dataset, model);


 Training data performance: 
MLBase.ROCNums{Int64}
  p = 13
  n = 90
  tp = 9
  tn = 88
  fp = 2
  fn = 4
precision: 0.8181818181818182
f1score: 0.75
recall: 0.6923076923076923
false positive rate: 0.022222222222222223
equal error rate: 0.16495726495726495

 Testing data performance: 
MLBase.ROCNums{Int64}
  p = 13
  n = 90
  tp = 5
  tn = 85
  fp = 5
  fn = 8
precision: 0.5
f1score: 0.43478260869565216
recall: 0.38461538461538464
false positive rate: 0.05555555555555555
equal error rate: 0.3354700854700855


In [15]:
# plot heatmap of the fit
xl = (minimum(X[1,:])-0.05, maximum(X[1,:]) + 0.05)
yl = (minimum(X[2,:])-0.05, maximum(X[2,:]) + 0.05)
p = scatter(X[1, tryhat.==1], X[2, tryhat.==1], c = :red, label = "predicted positive",
    xlims=xl, ylims = yl, title = "classification results and anomaly score contours")
scatter!(X[1, tryhat.==0], X[2, tryhat.==0], c = :green, label = "predicted negative",
    legend = (0.1, 0.7))

x = linspace(xl[1], xl[2], 30)
y = linspace(yl[1], yl[2], 30)
zz = zeros(size(y,1),size(x,1))
for i in 1:size(y, 1)
    for j in 1:size(x, 1)
        zz[i,j] = AnomalyDetection.anomalyscore(model, AnomalyDetection.Float.([x[j], y[i]]))
    end
end
contourf!(x, y, zz, c = :viridis)

display(p)
if !isinteractive()
    gui()
end

In [16]:
# what are the codes?

z1 = AnomalyDetection.getcode(model, X[:,1:30]).data
z2 = AnomalyDetection.getcode(model, X[:,31:60]).data
z3 = AnomalyDetection.getcode(model, X[:,61:90]).data
za = AnomalyDetection.getcode(model, X[:,91:end]).data

p = scatter(z1[1,:], z1[2,:], label = "first cluster")
scatter!(z2[1,:], z2[2,:], label = "second cluster")
scatter!(z3[1,:], z3[2,:], label = "third cluster")
scatter!(za[1,:], za[2,:], s = 10, label = "anomalous data")

display(p)
if !isinteractive()
    gui()
end

In [17]:
# plot the roc curve as well
ascore = AnomalyDetection.anomalyscore(model, X);
recvec, fprvec = AnomalyDetection.getroccurve(ascore, Y)

([1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0  …  0.615385, 0.538462, 0.461538, 0.384615, 0.384615, 0.307692, 0.230769, 0.153846, 0.0769231, 0.0769231], [1.0, 0.988889, 0.977778, 0.966667, 0.955556, 0.944444, 0.933333, 0.922222, 0.911111, 0.9  …  0.0111111, 0.0111111, 0.0111111, 0.0111111, 1.53003e-15, 1.53003e-15, 1.53003e-15, 1.53003e-15, 1.53003e-15, -0.0111111])

In [18]:
function plotroc(args...)
    # plot the diagonal line
    p = plot(linspace(0,1,100), linspace(0,1,100), c = :gray, alpha = 0.5, xlim = [0,1],
    ylim = [0,1], label = "", xlabel = "false positive rate", ylabel = "true positive rate",
    title = "ROC")
    for arg in args
        plot!(arg[1], arg[2], label = arg[3], lw = 2)
    end
    return p
end

plargs = [(fprvec, recvec, "VAE")]
display(plotroc(plargs...))
if !isinteractive()
    gui()
end

In [19]:
using MLBase: false_positive_rate, false_negative_rate
n = 21
alphavec = linspace(0,1,n)
eervec = zeros(n)
for i in 1:n
    model.alpha = alphavec[i]
    AnomalyDetection.setthreshold!(model, X)
    tryhat, tsthat, trroc, tstroc = AnomalyDetection.rocstats(dataset.data, dataset.labels,
        dataset.data, dataset.labels, model, verb = false)
    eervec[i] = (false_positive_rate(tstroc) + false_negative_rate(tstroc))/2
end

In [20]:
plot(alphavec, eervec, title = "equal error rate vs alpha",
    xlabel="alpha", ylabel = "EER")
if !isinteractive()
    gui()
end